<a href="https://colab.research.google.com/github/Mioooooer/ForAIColabUse/blob/main/open_musiclm_inference.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# open-musiclm inference
## Instructions
1. **Set your prompt text and audio duration** (in seconds) in the first cell.
2. Then go to **Runtime > Restart and run all.**
3. This notebook downloads the [checkpoints](https://github.com/zhvng/open-musiclm#checkpoints) from a [shared Google Drive folder](https://drive.google.com/drive/u/0/folders/1347glwEc-6XWulfU7NGrFrYTvTnjeVJE). You'll be prompted, "Allow this notebook to access your Google credentials?" Choose **"Allow."**
4. At the end of the notebook, you can **listen** to the generated audio inline, and **download** the wav file to your local machine.

In [ ]:
PROMPT = 'airship with classic Chinese building'
DURATION = 60

# Clones the open-musiclm repo

In [ ]:
!git clone https://github.com/zhvng/open-musiclm.git
%cd /content/open-musiclm

Cloning into 'open-musiclm'...
remote: Enumerating objects: 1433, done.
remote: Counting objects: 100% (224/224), done.
remote: Compressing objects: 100% (93/93), done.
remote: Total 1433 (delta 155), reused 178 (delta 129), pack-reused 1209
Receiving objects: 100% (1433/1433), 1.85 MiB | 18.59 MiB/s, done.
Resolving deltas: 100% (1004/1004), done.
/content/open-musiclm


# Downloads checkpoints

In [ ]:
def dl_drive_folder(folder_id):
    """
    Download shared Google Drive folder, from Colab notebook.
    
    You'll be prompted, "Allow this notebook to access your Google credentials?"
    Choose "Allow."

    PyDrive can be authenticated through Colab, but can't download from another user's shared Drive.
    PyDrive2 can download from another user's shared Drive, but can't be authenticated through Colab.
    This function accomplishes both by using a workaround. See URLs in the comments for more details.

    TODO: Use https://github.com/wkentaro/gdown instead for a simpler solution.
    """
    !pip install -q pydrive2

    import httplib2
    from pathlib import Path

    from google.colab import auth
    from oauth2client.client import GoogleCredentials
    from oauth2client.contrib.gce import AppAssertionCredentials
    from pydrive2.auth import GoogleAuth
    from pydrive2.drive import GoogleDrive

    # https://github.com/iterative/PyDrive2/issues/187
    old_local_webserver_auth = GoogleAuth.LocalWebserverAuth

    def LocalWebServerAuth(self, *args, **kwargs):
        if isinstance(self.credentials, AppAssertionCredentials):
            self.credentials.refresh(httplib2.Http())
            return
        return old_local_webserver_auth(self, *args, **kwargs)

    GoogleAuth.LocalWebserverAuth = LocalWebServerAuth

    # https://colab.research.google.com/notebooks/io.ipynb
    auth.authenticate_user()
    gauth = GoogleAuth()
    gauth.credentials = GoogleCredentials.get_application_default()
    drive = GoogleDrive(gauth)

    # https://stackoverflow.com/questions/58915550/pydrive-download-file-from-a-shared-drive/66450826#66450826
    # https://docs.iterative.ai/PyDrive2/quickstart/#return-file-id-via-file-title
    file_list = drive.ListFile({'q': f'"{folder_id}" in parents and trashed=false'}).GetList()
    for file in file_list:
        file_name = file['title']
        if not Path(file_name).exists():
            print(f'Downloading {file_name} ...')
            f = drive.CreateFile({'id': file['id']})
            f.GetContentFile(file_name)
    print('Done!')


dl_drive_folder('1347glwEc-6XWulfU7NGrFrYTvTnjeVJE')

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.7/44.7 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.9/57.9 kB 2.8 MB/s eta 0:00:00
Done!


# Installs requirements

In [ ]:
%%writefile requirements.txt
torch==2.0.0+cu117
torchvision==0.15.1+cu117
torchaudio==2.0.1+cu117
einops>=0.4
vector-quantize-pytorch>=0.10.15
librosa==0.10.0
torchlibrosa==0.1.0
ftfy
tqdm
transformers
encodec==0.1.1
gdown
accelerate>=0.17.0
beartype
joblib
h5py
scikit-learn==1.2.1
wget

Writing requirements.txt


In [ ]:
!pip install -q -r requirements.txt -f https://download.pytorch.org/whl/torch_stable.html

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 GB 984.3 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.1/6.1 MB 109.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.4/4.4 MB 83.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.2/42.2 kB 4.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 252.9/252.9 kB 27.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.1/53.1 kB 7.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 110.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 113.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 215.3/215.3 kB 27.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 720.2/720.2 kB 62.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.6/9.6 MB 118.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

# Runs script

In [ ]:
!python scripts/infer_top_match.py \
    '{PROMPT}' \
    --duration {DURATION} \
    --num_samples 2 \
    --num_top_matches 1 \
    --semantic_path semantic.transformer.14000.pt \
    --coarse_path coarse.transformer.18000.pt \
    --fine_path fine.transformer.24000.pt \
    --rvq_path clap.rvq.950_no_fusion.pt \
    --kmeans_path kmeans_10s_no_fusion.joblib \
    --model_config musiclm_large_small_context.json \
    --return_coarse_wave

2023-05-08 08:40:59.477770: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
Some weights of the model checkpoint at roberta-base were not used when initializing RobertaModel: ['lm_head.dense.weight', 'lm_head.layer_norm.weight', 'lm_head.layer_norm.bias', 'lm_head.dense.bias', 'lm_head.decoder.weight', 'lm_head.bias']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
/usr/local/lib/python3.10/dist-packages/torchaudio/transforms/_transforms.py:611: UserWarning: Argument 'onesided' has been deprecated and has no influence on the behavior o

# Gets results

In [ ]:
from glob import glob
from IPython.display import display, Audio

results = glob('results/*.wav')
for result in results:
    print(result)
    display(Audio(result))

results/airship with classic Chinese buildi_top_match_0.wav


In [ ]:
from google.colab import files

for result in results:
    files.download(result)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>